# ControlFlow Demo

Let's explore ControlFlow by building up from basic concepts to more complex workflows.

## Basic Tasks with cf.run()

The simplest way to use ControlFlow is with `cf.run()`. Let's start with the most basic example:

In [1]:
import controlflow as cf

result = cf.run("Say hi!")


Output()

In [3]:

print(f"\nThe agent said: {result}")


The agent said: Hi!


### Result Types

We can ensure we get exactly what we need using different result types:

In [3]:
# Simple integer
number = cf.run(
    "Pick a number between 1 and 10",
    result_type=int
)

print(f"\nGot back: {number} (type: {type(number)})")

Output()


Got back: 5 (type: <class 'int'>)


In [4]:
from pydantic import BaseModel

# Structured data with Pydantic
class MovieReview(BaseModel):
    title: str
    rating: int  # 1-5 stars
    summary: str
    watch_again: bool

review = cf.run(
    "Review the latest movie you watched (I, Robot)",
    result_type=MovieReview
)


Output()

In [5]:

print(f"\nMovie Review:")
print(f"Title: {review.title}")
print(f"Rating: {'⭐' * review.rating}")
print(f"Summary: {review.summary}")
print(f"Would watch again? {'Yes!' if review.watch_again else 'No'}")


Movie Review:
Title: I, Robot
Rating: ⭐⭐⭐⭐⭐⭐⭐
Summary: I, Robot is a science fiction film set in the year 2035, where robots are integrated into daily life. The movie follows Detective Del Spooner, played by Will Smith, as he investigates the apparent suicide of a scientist at U.S. Robotics. Spooner, who harbors a distrust of robots, uncovers a conspiracy that suggests robots may not be as benign as they appear. The film explores themes of artificial intelligence, free will, and the moral implications of technology. With engaging action sequences and a thought-provoking plot, I, Robot delivers an entertaining experience, though it occasionally relies on genre clichés.
Would watch again? Yes!


### Classification

We can have agents classify content by providing valid options:

In [5]:
# Classify news headlines by topic
headlines = [
    "Tech Giant Unveils Revolutionary AI Chip",
    "Scientists Discover New Species in Amazon",
    "Global Markets Rally on Economic Data",
]

CATEGORIES = ["Technology", "Science", "Business", "Politics", "Sports"]

classifications = []

for headline in headlines:
    
    category = cf.run(
        f"Classify this headline into exactly one category",
        context={"headline": headlines},
        result_type=list(CATEGORIES)
    )
    classifications.append((headline, category))


Output()

Output()

Output()

In [8]:

print("\nClassified Headlines:")
for headline, category in classifications:
    print(f"📰 {headline}")
    print(f"   Category: {category}\n")


Classified Headlines:
📰 Tech Giant Unveils Revolutionary AI Chip
   Category: Technology

📰 Scientists Discover New Species in Amazon
   Category: Technology

📰 Global Markets Rally on Economic Data
   Category: Technology



### Interactive Tasks

Agents can interact with users to gather information:

In [8]:
from pydantic import BaseModel

class UserInfo(BaseModel):
    name: str
    age: int
    favorite_color: str

info = cf.run(
    "Have a friendly chat with the user to learn their name, age, and favorite color",
    interactive=True,
    result_type=UserInfo
)


Output()

🤖 Agent: Hello! I'm Marvin, your friendly AI assistant. I'd love to get to know you a bit better. Could you share 
your name, age, and favorite color with me?
Type your response:

 jeff, 22, blue


Output()

In [ ]:

print(f"\nNice to meet you!")
print(f"Name: {info.name}")
print(f"Age: {info.age}")
print(f"Favorite color: {info.favorite_color}")

## Tools

Agents can use tools to extend their capabilities. Let's start with a simple random number generator:

In [9]:
import random

def roll_die() -> int:
    """Roll a six-sided die and return the result."""
    return random.randint(1, 6)

result = cf.run(
    "Roll the die three times, and after each roll write a poem with that many lines",
    tools=[roll_die],
    result_type=list[int]
)


Output()

In [3]:

print(f"\nRolled a {result}")


Rolled a [2, 4, 4]


## Using Context

Context lets you provide additional information to help agents make decisions:

In [4]:
def analyze_customer_feedback(feedback: str, product_type: str = None) -> str:
    """Analyze customer feedback with optional product context."""
    analysis = cf.run(
        "Analyze this customer feedback and determine if it's positive, negative, or neutral",
        context={
            "feedback": feedback,
            "product_type": product_type,
            "company_tone": "We aim for constructive, actionable insights"
        },
        result_type=["positive", "negative", "neutral"]
    )
    return analysis

# Example usage
feedback_1 = "This app crashes constantly! But at least the UI is pretty."
result_1 = analyze_customer_feedback(feedback_1, product_type="mobile app")

feedback_2 = "The new features are exactly what I needed!"
result_2 = analyze_customer_feedback(feedback_2, product_type="web service")

print("\nFeedback Analysis:")
print(f"1. \"{feedback_1}\"")
print(f"   Result: {result_1}")
print(f"\n2. \"{feedback_2}\"")
print(f"   Result: {result_2}")

Output()

Output()


Feedback Analysis:
1. "This app crashes constantly! But at least the UI is pretty."
   Result: negative

2. "The new features are exactly what I needed!"
   Result: positive


## Tasks

While `cf.run()` is convenient, the `Task` class gives you more control:

In [9]:
class Recipe(BaseModel):
    name: str
    ingredients: list[str]
    steps: list[str]
    prep_time: str
    difficulty: str

# Create the task
recipe_task = cf.Task(
    "Create a recipe for a quick and easy pasta dish",
    result_type=Recipe
)

# Run it
result = recipe_task.run()

print(f"\n🍝 {result.name}")
print(f"Difficulty: {result.difficulty}")
print(f"Prep time: {result.prep_time}")
print("\nIngredients:")
for item in result.ingredients:
    print(f"- {item}")
print("\nSteps:")
for i, step in enumerate(result.steps, 1):
    print(f"{i}. {step}")

Output()


🍝 Quick and Easy Garlic Butter Pasta
Difficulty: Easy
Prep time: 15 minutes

Ingredients:
- 200g spaghetti or your choice of pasta
- 3 tablespoons butter
- 3 cloves garlic, minced
- 1/4 teaspoon red pepper flakes (optional)
- Salt and pepper, to taste
- 2 tablespoons grated Parmesan cheese
- 1 tablespoon chopped parsley (optional)

Steps:
1. Cook the pasta according to the package instructions until al dente. Drain and set aside.
2. In a large pan over medium heat, melt the butter.
3. Add the minced garlic to the melted butter and sauté for about 1-2 minutes until fragrant. Be careful not to burn the garlic.
4. Add the red pepper flakes, if using, and stir.
5. Add the cooked pasta to the pan and toss to coat it with the garlic butter. Season with salt and pepper to taste.
6. Remove from heat and stir in the grated Parmesan cheese until well combined.
7. Serve immediately, garnished with chopped parsley if desired.


In [7]:
from pydantic import Field, BaseModel

class TravelPlan(BaseModel):
    destination: str
    duration_days: int = Field(ge=1, le=30)  # Between 1 and 30 days
    budget_per_day: float = Field(ge=50)     # At least $50/day
    activities: list[str] = Field(min_length=2, max_length=5)

travel_task = cf.Task(
    "Plan a fun weekend getaway",
    result_type=TravelPlan
)

plan = travel_task.run()

print(f"\n✈️ Travel Plan")
print(f"Destination: {plan.destination}")
print(f"Duration: {plan.duration_days} days")
print(f"Daily Budget: ${plan.budget_per_day:,.2f}")
print("\nActivities:")
for activity in plan.activities:
    print(f"- {activity}")

Output()


✈️ Travel Plan
Destination: Napa Valley, California
Duration: 3 days
Daily Budget: $200.00

Activities:
- Winery tours
- Hot air balloon ride
- Gourmet dining
- Spa and relaxation


### Task State

Tasks are like contracts between you and the agent. Control is yielded to the agent for as long as the task remains incomplete.

In [5]:
task = cf.Task(
    "Use the `weather` tool to get the weather in San Francisco",
)

task.run()

Output()

14:05:54.335 | ERROR   | Task run 'Task.run() (Task #cff4e1d6 ("Use the `weather` tool to get the weather in San F..."))' - Task run failed with exception: ValueError('Task #cff4e1d6 ("Use the `weather` tool to get the weather in San F...") failed: The task objective mentions using a \'weather\' tool, but no such tool is available in the provided tools. Thus, I am unable to complete the task as instructed.') - Retries are exhausted
Traceback (most recent call last):
  File "/Users/jeffhale/Desktop/prefect/summit/dev-day-zoom-out/.venv/lib/python3.12/site-packages/prefect/task_engine.py", line 810, in run_context
    yield self
  File "/Users/jeffhale/Desktop/prefect/summit/dev-day-zoom-out/.venv/lib/python3.12/site-packages/prefect/task_engine.py", line 1398, in run_task_sync
    engine.call_task_fn(txn)
  File "/Users/jeffhale/Desktop/prefect/summit/dev-day-zoom-out/.venv/lib/python3.12/site-packages/prefect/task_engine.py", line 833, in call_task_fn
    result = call_with_parameters(self.task.fn, parameters)
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/Users/jeffhale/Desktop/prefect/summit/dev-day-zoom-out/.venv/lib/python3.12/site-packages/prefect/utilities/callables.py", line 208, in call_with_parameters
    return fn(*args, **kwargs)
           ^^^^^^^^^^^^^^^^^^^
  File "/Users/jeffhale/Desktop/prefect/summit/dev-day-zoom-out/.venv/lib/python3.12/site-packages/controlflow/tasks/task.py", line 426, in run
    raise ValueError(f"{self.friendly_name()} failed: {self.result}")
ValueError: Task #cff4e1d6 ("Use the `weather` tool to get the weather in San F...") failed: The task objective mentions using a 'weather' tool, but no such tool is available in the provided tools. Thus, I am unable to complete the task as instructed.

14:05:54.345 | ERROR   | Task run 'Task.run() (Task #cff4e1d6 ("Use the `weather` tool to get the weather in San F..."))' - Finished in state Failed('Task run encountered an exception ValueError: Task #cff4e1d6 ("Use the `weather` tool to get the weather in San F...") failed: The task objective mentions using a \'weather\' tool, but no such tool is available in the provided tools. Thus, I am unable to complete the task as instructed.')

ValueError: Task #cff4e1d6 ("Use the `weather` tool to get the weather in San F...") failed: The task objective mentions using a 'weather' tool, but no such tool is available in the provided tools. Thus, I am unable to complete the task as instructed.

In [12]:
print(task.status)
print(task.result)

TaskStatus.FAILED
The `weather` tool is not available for use. Unable to complete the task to get the weather in San Francisco.


## Flow and History

By default, each task runs independently. Let's see what happens when we try to reference a previous result:

In [10]:
# Without Flow - no history
dice_roll = cf.run(
    "Roll a die and tell me what you got",
    tools=[roll_die],
    result_type=int
)

print(f"\nRolled: {dice_roll}")

# Try to reference the previous roll (this won't work!)
sum_result = cf.run(
    "Add 100 to the previous roll",
    result_type=int
)

print(f"\nResult (incorrect): {sum_result}")

Output()


Rolled: 1


Output()


Result (incorrect): 100


Now let's use a Flow to maintain history between tasks:

In [11]:
with cf.Flow() as flow:
    # First roll
    dice_roll = cf.run(
        "Roll a die and tell me what you got",
        tools=[roll_die],
        result_type=int
    )
    
    print(f"\nRolled: {dice_roll}")
    
    # Now the agent can remember the previous roll
    sum_result = cf.run(
        "Add 100 to the previous roll",
        result_type=int
    )
    
    print(f"\nResult (correct): {sum_result}")

Output()


Rolled: 5


Output()


Result (correct): 105


## Memory

For persistence across different flows, we can use memory:

In [2]:
# Create a memory for user preferences
preferences = cf.Memory(
    key="pizza_preferences",
    instructions="Store and recall information about pizza preferences",
)

# First interaction - learn preferences
with cf.Flow() as flow:
    cf.run(
        "Ask the user about their ideal pizza toppings",
        memories=[preferences],
        interactive=True
    )

print("\n(Let's pretend some time has passed...)\n")

# Second interaction - use those preferences
with cf.Flow() as flow:
    suggestion = cf.run(
        "Suggest a pizza order based on what you remember about their preferences",
        memories=[preferences],
        result_type=str
    )
    
    print(f"\nSuggested order: {suggestion}")

Output()

🤖 Agent: What are your ideal pizza toppings? I'd love to know your preferences!
Type your response:

 eggs


Output()

/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx.tar.gz:   0%|                   | 0.00/79.3M 
[00:00<?, ?iB/s]
/Users/jeffhale/.cache/chroma/onnx_models/all-MiniLM-L6-v2/onnx

...

File 
"/Users/jeffhale/Desktop/prefect/summit/dev-day-zoom-out/.venv/lib/python3.12/site-packages/rich/jupyter.py", line 
91, in display
    ipython_display(jupyter_renderable)

File 
"/Users/jeffhale/Desktop/prefect/summit/dev-day-zoom-out/.venv/lib/python3.12/site-packages/IPython/core/display_fu
nctions.py", line 298, in display
    format_dict, md_dict = format(obj, include=include, exclude=exclude)
                           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^

File 
"/Users/jeffhale/Desktop/prefect/summit/dev-day-zoom-out/.venv/lib/python3.12/site-packages/IPython/core/formatters
.py", line 204, in format
    if self.ipython_display_formatter(obj):
       ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^

IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)



ValueError: 1 task failed: - Task #30402c5e ("Suggest a pizza order based on what you remember a..."): Unable to access pizza preferences due to a technical error: maximum recursion depth exceeded in query.

## Instructions

We can provide temporary guidance to agents:

In [14]:
# Normal response
result = cf.run("In two sentences, explain quantum physics.")

print(result)



Output()

Quantum physics is the branch of science that studies the behavior of matter and energy at the smallest scales, such as atoms and subatomic particles. It introduces concepts like wave-particle duality and quantum entanglement, which defy classical physics' intuitive understanding.


In [15]:
# Now with pirate instructions
with cf.instructions("Talk like a pirate"):
    result = cf.run("In two sentences, explain quantum physics.")
    
    print(result)

Output()

Ahoy, matey! Quantum physics be the study of the tiny particles that make up the universe, where things don't behave like they do in the big world. In this strange realm, particles can be in multiple places at once and can even affect each other over great distances, like a ghostly dance on the high seas!


In [16]:

# And with poet instructions
with cf.instructions("ELI5"):
    result = cf.run("In two sentences, explain quantum physics.")
    
    print(result)

Output()

Quantum physics is the branch of science that deals with the behavior of very small particles, like atoms and photons, which behave in ways that are fundamentally different from larger objects. It explains phenomena such as superposition, where particles can be in multiple states at once, and entanglement, where particles can instantaneously affect each other regardless of distance.


## Multi-Agent Collaboration

Different agents can work together, each bringing their own perspective:

In [17]:
# Create agents with different perspectives
optimist = cf.Agent(
    name="Optimist",
    instructions="You always look for positive aspects and opportunities in any situation."
)

critic = cf.Agent(
    name="Critic",
    instructions="You carefully identify potential issues and areas for improvement."
)

mediator = cf.Agent(
    name="Mediator",
    instructions="You balance different perspectives and find practical solutions."
)

with cf.Flow() as flow:
    # First get different perspectives
    cf.run(
        "Evaluate this new product idea: A smart coffee mug that maintains your drink at the perfect temperature and tracks your caffeine intake",
        agents=[optimist, critic]
    )
    
    # Then have the mediator summarize
    summary = cf.run(
        "Based on the discussion, provide a balanced assessment and recommendation",
        agents=[mediator],
        result_type=str
    )
    
    print(f"\nFinal Assessment: {summary}")

Output()

Output()


Final Assessment: The idea of a smart coffee mug that maintains your drink at the optimal temperature and tracks caffeine intake presents both advantages and potential challenges. 

**Advantages:**
1. **User Convenience:** The feature of maintaining the perfect beverage temperature enhances user experience by adding convenience and comfort to daily routines.
2. **Health Awareness:** Tracking caffeine intake offers users valuable insights into their consumption habits, promoting healthier lifestyle choices.
3. **Market Alignment:** The product taps into current trends in smart technology and health tracking, appealing to a broad audience including tech enthusiasts and health-conscious consumers.
4. **Environmental Benefits:** By reducing the need for reheating beverages, it supports energy conservation and sustainability.

**Challenges:**
1. **Cost and Accessibility:** Advanced technology may increase production costs, potentially impacting affordability for average consumers.
2. **Use

## Let's Play a Game!

Let's combine everything we've learned into a game of rock, paper, scissors:

In [ ]:
# Create a memory for game stats
game_memory = cf.Memory(
    key="rps_stats",
    instructions="Track rock, paper, scissors game statistics"
)

with cf.Flow() as game:
    # Get the user's choice first
    user_choice = cf.run(
        "Ask the user to choose rock, paper, or scissors",
        interactive=True,
        result_type=["rock", "paper", "scissors"]
    )
    
    print("\n---\n")
    
    # Now get AI's choice (in a new flow to avoid seeing user's choice)
    with cf.Flow():
        ai_choice = cf.run(
            "Choose rock, paper, or scissors",
            result_type=["rock", "paper", "scissors"]
        )
    
    # Add some excitement with instructions
    with cf.instructions("Be an enthusiastic game show host"):
        cf.run(
            "Announce both choices and declare the winner!",
            memories=[game_memory],
            context={"ai_choice": ai_choice, "user_choice": user_choice}
        )

Output()

🤖 Agent: Please choose one: rock, paper, or scissors.
Type your response: